In [1]:
import numpy as np
import matplotlib.pyplot as plt
import pickle
import time

import pandas as pd
from deltaNets import combustionML
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
from dataScaling import LogScaler, AtanScaler, NoScaler
from boost_test import test_data

/home/eg/anaconda3/envs/my_dev/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


precision: float32
Running Cantera version: 2.3.0
Running Cantera version: 2.3.0
Running Cantera version: 2.3.0


In [2]:
from reactor_ode_delta import ignite_post, data_gen_f

# T = np.random.rand(30) * 1200 + 1001
T = np.linspace(1001, 2000, 40)

n_r = np.random.rand(1) * 2 + 0.3
# n_r = np.random.rand(30) * 20
n_s = np.linspace(0.3, 8, 30)
n_l = np.linspace(0, 30, 30)

n = np.unique(np.concatenate((n_s, n_l,n_r)))[1:]
n=n[n>0.4]
XX, YY = np.meshgrid(T, n)
ini = np.concatenate((XX.reshape(-1, 1), YY.reshape(-1, 1)), axis=1)

df_x_input_org, df_y_target_org = data_gen_f(ini, 'H2')
pickle.dump((df_x_input_org, df_y_target_org), open('data/x_y_org.p', 'wb'))

multiprocessing:

/home/eg/anaconda3/envs/my_dev/lib/python3.6/site-packages/scipy/integrate/_ode.py:1009: UserWarning: vode: Illegal input detected. (See printed message.)
  self.messages.get(istate, unexpected_istate_msg)))
/home/eg/anaconda3/envs/my_dev/lib/python3.6/site-packages/scipy/integrate/_ode.py:1009: UserWarning: vode: Illegal input detected. (See printed message.)
  self.messages.get(istate, unexpected_istate_msg)))
/home/eg/anaconda3/envs/my_dev/lib/python3.6/site-packages/scipy/integrate/_ode.py:1009: UserWarning: vode: Illegal input detected. (See printed message.)
  self.messages.get(istate, unexpected_istate_msg)))
/home/eg/anaconda3/envs/my_dev/lib/python3.6/site-packages/scipy/integrate/_ode.py:1009: UserWarning: vode: Illegal input detected. (See printed message.)
  self.messages.get(istate, unexpected_istate_msg)))


  373.605 seconds


## pca visualisation

In [3]:
df_x_org, df_y_org = pickle.load(open('data/x_y_org.p', 'rb'))
columns = df_x_org.columns
# train_features = columns.drop(['f','N2','dt','Rho','cp','Hs'])
train_features = columns.drop(['f','dt','Rho','cp','Hs'])

# initial conditions
n_H2 = sorted(list(map(float, set(df_x_org['f']))))
n_H2 = np.asarray(n_H2).reshape(-1, 1)

df_x = df_x_org[train_features]
df_y = df_y_org[train_features]

pca= PCA(n_components=3) # pca for 3D visualization
df_x_s=df_x.sample(frac=1) # take 10% data
# idx = (df_y/df_x <1.2).all(1)
# df_x_s = df_x.loc[idx]

# scaler = NoScaler()
scaler = StandardScaler()
train=pca.fit_transform(scaler.fit_transform(df_x_s))
train = np.hstack((train,0*np.ones((train.shape[0],1)))) # add a label 

## functions

In [4]:
def delta_filter(df_in,delta_in):
    delta = delta_in
    mesh = np.round(df_in[['x','y','z']]/delta)
    mesh_ijk = [tuple(r) for i,r in mesh.iterrows()]
    df_out=df_in
    df_out['ijk'] = mesh_ijk
    df_out=df_out.drop_duplicates('ijk',keep='first')
    return df_out


def new_data_gen(df_in,pca_model,scaler_model,df_x_columns):
    new_data=pca_model.inverse_transform(df_in[['x','y','z']])
    new_data=scaler_model.inverse_transform(new_data)
    new_dx = pd.DataFrame(new_data,columns=df_x_columns)
    new_dx = new_dx[(new_dx>=0).all(1)]
# new_dx = new_dx[(new_dx<0).any(1)]
    pickle.dump(new_dx, open('data/test_random_delta.p', 'wb'))
    new_pca = pd.DataFrame(pca_model.transform(scaler_model.transform(new_dx)),columns=['x','y','z'])
    return new_pca
       
    

In [5]:
delta = 0.01
mesh_train = np.round(train / delta)[:,:3]
train_ijk=[tuple(i) for i in mesh_train.tolist()]
# train = np.hstack((train,train_ijk)) # add a label 

In [6]:
# test data
ns=[0.5,2,15]
test=np.empty((0,train.shape[1]))
for i in ns:
    ode_o, ode_n = test_data(1501, i, columns)
    ode_o = ode_o[train_features]
    tmp = np.hstack((pca.transform(scaler.transform(ode_o)),i*np.ones((ode_o.shape[0],1))))  
    test = np.append(test,tmp,axis=0)

mesh_test = np.round(test/delta)[:,:3]
test_ijk=[tuple(i) for i in mesh_test.tolist()]

0.041100871286573026 Y_H2= [0.00036722]
0.002585421123201214 Y_H2= [0.00412684]
0.0023755605905325995 Y_H2= [0.14933596]


In [7]:
#n_sample=100_000
n_sample=0
if n_sample >0:
    idx_sample=np.random.choice(train.shape[0],n_sample)
    train=train[idx_sample]
    train_ijk=list(train_ijk[i] for i in idx_sample)
df_pca=pd.DataFrame(np.vstack((train,test)),columns=['x','y','z','label'])
df_pca['ijk']=train_ijk+test_ijk
df_pca=df_pca.drop_duplicates('ijk',keep='first')
selected=df_pca[df_pca['label']==0].index.values

In [8]:
import plotly.plotly as py
import plotly.offline as pyoff
import plotly.graph_objs as go
import plotly.tools as tls

# df_pca=df_pca.sample(frac=0.1)
df_pca_react=df_pca[df_pca['label']<50]
df_pca_s=df_pca_react.sample(10_000)

fig_db = {
    'data': [
        {'x': df_pca_s[df_pca_s['label']==label]['x'],
         'y': df_pca_s[df_pca_s['label']==label]['y'],
         'z': df_pca_s[df_pca_s['label']==label]['z'],
         'type':'scatter3d', 'mode': 'markers', 'marker':{'size':2}, 'name': label} for label in set(df_pca_react['label'])
        
    ],
    'layout': {
    }
}
pyoff.iplot(fig_db, filename='multiple-scatter')

In [9]:
print(len(selected),df_x.shape[0],len(selected)/df_x.shape[0])

879068 3338717 0.2632951520000048


In [10]:
pickle.dump((df_x_org.loc[selected], df_y_org.loc[selected]), open('data/x_y_org_pca_reduced.p', 'wb'))

## interpolation

In [11]:
from scipy.interpolate import griddata
df_pca['value']=np.ones((df_pca.shape[0],1))*100
xrg=np.linspace(df_pca['x'].min(),df_pca['x'].max(),200)
yrg=np.linspace(df_pca['y'].min(),df_pca['y'].max(),100)
zrg=np.linspace(df_pca['z'].min(),df_pca['z'].max(),100)
xx,yy,zz=np.meshgrid(xrg,yrg,zrg)

xx=xx.reshape(-1,1)
yy=yy.reshape(-1,1)
zz=zz.reshape(-1,1)
a=np.hstack([xx,yy,zz])
# b=np.vstack([df_pca[['x','y']],a[:,:2]])
# test_value=griddata(df_pca[['x','y']].values,df_pca['value'].values,df_pca[['x','y']].values,method='linear')
test_value=griddata(df_pca[['x','y','z']],df_pca['value'],a,method='linear')

In [12]:
df_test_all=pd.DataFrame(a,columns=['x','y','z'])
df_test=pd.DataFrame(a,columns=['x','y','z'])
df_test_all['label']=test_value
df_test['label']=test_value

if df_test.shape[0]>10_000:
    df_test=df_test.sample(10_000)
fig_db = {
    'data': [
        {'x': df_test[df_test['label']>0]['x'],
         'y': df_test[df_test['label']>0]['y'],
         'z': df_test[df_test['label']>0]['z'],
         'type':'scatter3d', 'mode': 'markers', 'marker':{'size':2}, 'name': 100} 
    ],
    'layout': {
    }
}
pyoff.iplot(fig_db, filename='multiple-scatter')

In [13]:
c=df_test_all[df_test_all['label']>0][['x','y','z']]
new_data=pca.inverse_transform(c)
df_x.columns
new_data=scaler.inverse_transform(new_data)
new_dx = pd.DataFrame(new_data,columns=df_x.columns)
new_dx = new_dx[(new_dx>=0).all(1)]
# new_dx = new_dx[(new_dx<0).any(1)]
pickle.dump(new_dx, open('data/test_griddata.p', 'wb'))
new_pca = pd.DataFrame(pca.transform(scaler.transform(new_dx)),columns=['x','y','z'])
new_pca.shape

(321463, 3)

In [14]:

if new_pca.shape[0]>10_000:
    new_pca=new_pca.sample(10_000)

fig_db = {
    'data': [
        {'x': df_pca_s[df_pca_s['label']==0]['x'],
         'y': df_pca_s[df_pca_s['label']==0]['y'],
         'z': df_pca_s[df_pca_s['label']==0]['z'],
         'type':'scatter3d', 'mode': 'markers', 'marker':{'size':2}, 'name': 0},
        {'x': new_pca['x'],
         'y': new_pca['y'],
         'z': new_pca['z'],
         'type':'scatter3d', 'mode': 'markers', 'marker':{'size':2}, 'name': 100},
         
        
    ],
    'layout': {
    }
}
pyoff.iplot(fig_db, filename='multiple-scatter')

In [15]:
import plotly.plotly as py
import plotly.offline as pyoff
import plotly.graph_objs as go
import plotly.tools as tls

# df_pca=df_pca.sample(frac=0.1)
# df_pca_s=df_pca.sample(10_000)

fig_db = {
    'data': [
        {'x': df_pca_s['x'],
         'y': df_pca_s['y'],
         'z': df_pca_s['z'],
         'type':'scatter3d', 'mode': 'markers', 'marker':{'size':2}, 'name': 0} 
        
    ],
    'layout': {
    }
}
pyoff.iplot(fig_db, filename='multiple-scatter')

## random shift

In [16]:
df_pca_r_1=df_pca[['x','y','z']]*(1+delta*(2*np.random.rand()-1))
# pds = [df_pca[['x','y','z']]*(1+1*delta*(2*np.random.rand()-1)) for i in range(10)]
pds = [df_pca[['x','y','z']]+1*delta*(2*np.random.rand()-1) for i in range(20)]

df_pca_r=pd.concat(pds,ignore_index=True)
# delta = 0.01

# mesh_r = np.round(df_pca_r.values / delta)[:,:3]
# r_ijk=[tuple(i) for i in mesh_r.tolist()]
# df_pca_r['ijk']=r_ijk 

# df_pca_r=df_pca_r.drop_duplicates('ijk',keep='first')
# df_pca_r=df_pca_r.sample(10_000)

In [17]:
# x1=pd.concat([df_pca[['x','y','z','ijk']],df_pca_r],ignore_index=True)
# x2=delta_filter(x1,0.01)
# x2=x2[df_pca.shape[0]:]
# a=delta_filter(df_pca_r,0.01)
# b=new_data_gen(a,pca,scaler,df_x.columns)
b=new_data_gen(df_pca_r,pca,scaler,df_x.columns)

b=pd.concat([df_pca[['x','y','z']],b],ignore_index=True)
b=delta_filter(b,delta)
b=b[df_pca.shape[0]:]
b=new_data_gen(b,pca,scaler,df_x.columns)
c=b
b=b.sample(10_000)
df_pca_r=df_pca_r.sample(10_000)

In [18]:
fig_db = {
    'data': [
        {'x': df_pca_r['x'],
         'y': df_pca_r['y'],
         'z': df_pca_r['z'],
         'type':'scatter3d', 'mode': 'markers', 'marker':{'size':2}, 'name': 'new'},
        {'x': df_pca_s['x'],
         'y': df_pca_s['y'],
         'z': df_pca_s['z'],
         'type':'scatter3d', 'mode': 'markers', 'marker':{'size':2}, 'name': 'old'},
        {'x': b['x'],
         'y': b['y'],
         'z': b['z'],
         'type':'scatter3d', 'mode': 'markers', 'marker':{'size':2}, 'name': 'good'} 
        
    ],
    'layout': {
    }
}
pyoff.iplot(fig_db, filename='multiple-scatter')

In [19]:
pca

PCA(copy=True, iterated_power='auto', n_components=3, random_state=None,
  svd_solver='auto', tol=0.0, whiten=False)